# Import

In [ ]:
from Recommenders.Recommender_import_list import *

Tensorflow is not available


In [ ]:
from Data_manager.DataSplitter_leave_k_out import DataSplitter_leave_k_out
from Recommenders.Incremental_Training_Early_Stopping import Incremental_Training_Early_Stopping
from Recommenders.BaseCBFRecommender import BaseItemCBFRecommender, BaseUserCBFRecommender
from Evaluation.Evaluator import EvaluatorHoldout

In [ ]:
import traceback
import os
import scipy
import numpy as np
import pandas as pd
import scipy.sparse as sps

from pandas_profiling import ProfileReport

In [ ]:
SEED = 42
np.random.seed(SEED)

# Data Loading and Analysis

In [ ]:
!ls ./Dataset

alg_sample_submission.csv  data_ICM_genre.csv	       data_train.csv
data_ICM_channel.csv	   data_ICM_subgenre.csv
data_ICM_event.csv	   data_target_users_test.csv


In [ ]:
data_file_path = "./Dataset"

URM_path = os.path.join(data_file_path, "data_train.csv")
ICM_channel_path = os.path.join(data_file_path, "data_ICM_channel.csv")
ICM_event_path = os.path.join(data_file_path, "data_ICM_event.csv")
ICM_genre_path = os.path.join(data_file_path, "data_ICM_genre.csv")
ICM_subgenre_path = os.path.join(data_file_path, "data_ICM_subgenre.csv")

## Load URM

In [ ]:
URM_all_dataframe = pd.read_csv(filepath_or_buffer=URM_path, 
                                sep=",",
                                dtype={0:int, 1:int, 2:int},
                                engine='python')

URM_all_dataframe.columns = ["UserID", "ItemID", "Interaction"]

In [ ]:
URM_all_dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5285664 entries, 0 to 5285663
Data columns (total 3 columns):
 #   Column       Dtype
---  ------       -----
 0   UserID       int64
 1   ItemID       int64
 2   Interaction  int64
dtypes: int64(3)
memory usage: 121.0 MB


In [ ]:
URM_all_dataframe.head(10)

UserID  ItemID  Interaction
0       0      53            1
1       0     209            1
2       0     223            1
3       0     249            1
4       0     435            1
5       0     460            1
6       0     652            1
7       0     960            1
8       0     973            1
9       0    1103            1

In [ ]:
URM_all_dataframe.nunique()

UserID         13650
ItemID         18059
Interaction        1
dtype: int64

In [ ]:
len(URM_all_dataframe.UserID)

5285664

In [ ]:
len(URM_all_dataframe.ItemID)

5285664

In [ ]:
sparsity = '{:.6%}'.format(len(URM_all_dataframe) / (URM_all_dataframe.UserID.nunique() * URM_all_dataframe.ItemID.nunique()))
print('This is an estimate of the sparsity of the URM: ', sparsity) 

This is an estimate of the sparsity of the URM:  2.144239%


In [ ]:
profile = ProfileReport(URM_all_dataframe, title="Pandas Profiling Report", explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

There are no duplicates or missing cells. Most importantly (since we expected a clead dataset) we have a histogram that show us the distribution of the *UserID*, and *ItemID*, and we can notice that the distribution is pretty even.

## Load ICM

### ICM Genre

In [ ]:
ICM_genre_dataframe = pd.read_csv(filepath_or_buffer=ICM_genre_path, 
                            sep=",", 
                            dtype={0:int, 1:int, 2:int},
                            engine='python')

ICM_genre_dataframe.columns = ["ItemID", "GenreID", "Interaction"]

In [ ]:
ICM_genre_dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17991 entries, 0 to 17990
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   ItemID       17991 non-null  int64
 1   GenreID      17991 non-null  int64
 2   Interaction  17991 non-null  int64
dtypes: int64(3)
memory usage: 421.8 KB


In [ ]:
ICM_genre_dataframe.head(10)

ItemID  GenreID  Interaction
0       0        3            1
1       1        3            1
2       2        6            1
3       3        0            1
4       3        1            1
5       4        4            1
6       5        3            1
7       6        7            1
8       7        6            1
9       8        4            1

In [ ]:
ICM_genre_dataframe.nunique()

ItemID         17500
GenreID            8
Interaction        1
dtype: int64

In [ ]:
len(ICM_genre_dataframe.ItemID)

17991

In [ ]:
len(ICM_genre_dataframe.GenreID)

17991

In [ ]:
sparsity = '{:.6%}'.format(len(ICM_genre_dataframe) / (ICM_genre_dataframe.ItemID.nunique() * ICM_genre_dataframe.GenreID.nunique()))
print('This is an estimate of the sparsity of the ICM genre: ', sparsity) 

This is an estimate of the sparsity of the ICM genre:  12.850714%


In [ ]:
profile = ProfileReport(ICM_genre_dataframe, title="Pandas Profiling Report", explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

There are no duplicates or missing cells. Most importantly (since we expected a clead dataset) we have a histogram that show us the distribution of the *ItemID*, and *GenreID*, and we can notice that the distribution of the *ItemID* is pretty even, instead the distribution of the *GenreID* is not evenly distributed accross the different genres.

### ICM Subgenre

In [ ]:
ICM_subgenre_dataframe = pd.read_csv(filepath_or_buffer=ICM_subgenre_path, 
                            sep=",", 
                            dtype={0:int, 1:int, 2:int},
                            engine='python')

ICM_subgenre_dataframe.columns = ["ItemID", "SubgenreID", "Interaction"]

In [ ]:
ICM_subgenre_dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18057 entries, 0 to 18056
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   ItemID       18057 non-null  int64
 1   SubgenreID   18057 non-null  int64
 2   Interaction  18057 non-null  int64
dtypes: int64(3)
memory usage: 423.3 KB


In [ ]:
ICM_subgenre_dataframe.head(10)

ItemID  SubgenreID  Interaction
0       0          70            1
1       1          27            1
2       2          40            1
3       3          50            1
4       4          62            1
5       5           3            1
6       6          99            1
7       7         102            1
8       8          62            1
9       9          61            1

In [ ]:
ICM_subgenre_dataframe.nunique()

ItemID         17572
SubgenreID       113
Interaction        1
dtype: int64

In [ ]:
len(ICM_subgenre_dataframe.ItemID)

18057

In [ ]:
len(ICM_subgenre_dataframe.SubgenreID)

18057

In [ ]:
sparsity = '{:.6%}'.format(len(ICM_subgenre_dataframe) / (ICM_subgenre_dataframe.ItemID.nunique() * ICM_subgenre_dataframe.SubgenreID.nunique()))
print('This is an estimate of the sparsity of the ICM genre: ', sparsity) 

This is an estimate of the sparsity of the ICM genre:  1%


In [ ]:
profile = ProfileReport(ICM_subgenre_dataframe, title="Pandas Profiling Report", explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

There are no duplicates or missing cells. Most importantly (since we expected a clead dataset) we have a histogram that show us the distribution of the *ItemID*, and *SubgenreID*, and we can notice that the distribution of the *ItemID* is pretty even, instead the distribution of the *SubgenreID* is not evenly distributed accross the different subgenres.

### ICM Event

In [ ]:
ICM_event_dataframe = pd.read_csv(filepath_or_buffer=ICM_event_path, 
                            sep=",", 
                            dtype={0:int, 1:int, 2:int},
                            engine='python')

ICM_event_dataframe.columns = ["ItemID", "EventID", "Interaction"]

In [ ]:
ICM_event_dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 358070 entries, 0 to 358069
Data columns (total 3 columns):
 #   Column       Non-Null Count   Dtype
---  ------       --------------   -----
 0   ItemID       358070 non-null  int64
 1   EventID      358070 non-null  int64
 2   Interaction  358070 non-null  int64
dtypes: int64(3)
memory usage: 8.2 MB


In [ ]:
ICM_event_dataframe.head(10)

ItemID  EventID  Interaction
0       0   121781            1
1       1   150102            1
2       1   349614            1
3       2     9174            1
4       2    20833            1
5       2   251794            1
6       3    81458            1
7       4    84041            1
8       5     7823            1
9       5    50941            1

In [ ]:
ICM_event_dataframe.nunique()

ItemID          17967
EventID        347825
Interaction         1
dtype: int64

In [ ]:
len(ICM_event_dataframe.ItemID)

358070

In [ ]:
len(ICM_event_dataframe.EventID)

358070

In [ ]:
sparsity = '{:.6%}'.format(len(ICM_event_dataframe) / (ICM_subgenre_dataframe.ItemID.nunique() * ICM_event_dataframe.EventID.nunique()))
print('This is an estimate of the sparsity of the ICM genre: ', sparsity) 

This is an estimate of the sparsity of the ICM genre:  0.005858%


In [ ]:
profile = ProfileReport(ICM_event_dataframe, title="Pandas Profiling Report", explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

There are no duplicates or missing cells. Most importantly (since we expected a clead dataset) we have a histogram that show us the distribution of the *ItemID*, and *EventID*, and we can notice that the distribution of the *EventID* is even (**Uniform**), instead the distribution of the *ItemID* is not evenly distributed accross the different *EventIDs*.

### ICM Channel

In [ ]:
ICM_channel_dataframe = pd.read_csv(filepath_or_buffer=ICM_channel_path, 
                            sep=",", 
                            dtype={0:int, 1:int, 2:int},
                            engine='python')

ICM_channel_dataframe.columns = ["ItemID", "ChannelID", "Interaction"]

In [ ]:
ICM_channel_dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24520 entries, 0 to 24519
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   ItemID       24520 non-null  int64
 1   ChannelID    24520 non-null  int64
 2   Interaction  24520 non-null  int64
dtypes: int64(3)
memory usage: 574.8 KB


In [ ]:
ICM_channel_dataframe.head(10)

ItemID  ChannelID  Interaction
0       0         23            1
1       1         30            1
2       2         38            1
3       2         53            1
4       3         51            1
5       4         99            1
6       5        152            1
7       6        115            1
8       7        173            1
9       8         36            1

In [ ]:
ICM_channel_dataframe.nunique()

ItemID         17707
ChannelID        213
Interaction        1
dtype: int64

In [ ]:
len(ICM_channel_dataframe.ItemID)

24520

In [ ]:
len(ICM_channel_dataframe.ChannelID)

24520

In [ ]:
sparsity = '{:.6%}'.format(len(ICM_channel_dataframe) / (ICM_channel_dataframe.ItemID.nunique() * ICM_channel_dataframe.ChannelID.nunique()))
print('This is an estimate of the sparsity of the ICM genre: ', sparsity) 

This is an estimate of the sparsity of the ICM genre:  0.650124%


In [ ]:
profile = ProfileReport(ICM_channel_dataframe, title="Pandas Profiling Report", explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

There are no duplicates or missing cells. Most importantly (since we expected a clead dataset) we have a histogram that show us the distribution of the *ItemID*, and *ChannelID*, and we can notice that the distribution of the *ItemID* is pretty even, instead the distribution of the *ChannelID* is not evenly distributed accross the different subgenres.

# Da vedere

In [ ]:
n_features = len(ICM_genre_dataframe["GenreID"].unique())

print ("Number of genres:\t\t\t {}\nNumber of item-genre tuples: \t\t{}".format(n_features, len(ICM_genre_dataframe)))
print ("Average number of features for item: {}".format(len(ICM_genre_dataframe)/n_features))

Number of genres:			 8
Number of item-genre tuples: 		17991
Average number of features for item: 2248.875


The average value has not much sense since the number of items for different genres are very much unbalanced.

## Data Analysis

Retrieving the new indexing of the users and the items

In [ ]:
user_original_ID_to_index_dict = {}

for user_id in URM_all_dataframe["UserID"].unique():
    user_original_ID_to_index_dict[user_id] = len(user_original_ID_to_index_dict)  

print("Unique user_id in the URM are {}".format(len(user_original_ID_to_index_dict)))
    
#for user_id in ICM_dataframe["UserID"].unique():
#    if user_id not in user_original_ID_to_index_dict:
#        user_original_ID_to_index_dict[user_id] = len(user_original_ID_to_index_dict)
        
#print("Unique user_id in the URM and ICM are {}".format(len(user_original_ID_to_index_dict)))

Unique user_id in the URM are 13650


In [ ]:
item_original_ID_to_index_dict = {}

for item_id in URM_all_dataframe["ItemID"].unique():
    item_original_ID_to_index_dict[item_id] = len(item_original_ID_to_index_dict)

print("Unique item_id in the URM are {}".format(len(item_original_ID_to_index_dict)))
    
#for item_id in ICM_dataframe["ItemID"].unique():
#    if item_id not in item_original_ID_to_index_dict:
#        item_original_ID_to_index_dict[item_id] = len(item_original_ID_to_index_dict)
        
#print("Unique item_id in the URM and ICM are {}".format(len(item_original_ID_to_index_dict)))

Unique item_id in the URM are 18059


In [ ]:
feature_original_ID_to_index_dict = {}

for feature_id in ICM_dataframe["FeatureID"].unique():
    feature_original_ID_to_index_dict[feature_id] = len(feature_original_ID_to_index_dict)

print("Unique feature_id in the URM are {}".format(len(feature_original_ID_to_index_dict)))

NameError: ignored

In [ ]:
dict(sorted(item_original_ID_to_index_dict.items(), key=lambda item: item[1]))

{53: 0,
 209: 1,
 223: 2,
 249: 3,
 435: 4,
 460: 5,
 652: 6,
 960: 7,
 973: 8,
 1103: 9,
 1215: 10,
 1267: 11,
 1418: 12,
 1455: 13,
 1461: 14,
 1496: 15,
 1782: 16,
 1964: 17,
 2083: 18,
 2307: 19,
 2489: 20,
 2678: 21,
 2844: 22,
 2886: 23,
 2974: 24,
 3065: 25,
 3136: 26,
 3140: 27,
 3473: 28,
 3492: 29,
 3544: 30,
 3619: 31,
 3830: 32,
 3942: 33,
 4081: 34,
 4292: 35,
 4365: 36,
 4438: 37,
 4522: 38,
 4571: 39,
 4582: 40,
 4607: 41,
 5051: 42,
 5134: 43,
 5273: 44,
 5299: 45,
 5300: 46,
 5403: 47,
 5414: 48,
 5665: 49,
 5793: 50,
 5925: 51,
 5951: 52,
 6006: 53,
 6112: 54,
 6170: 55,
 6177: 56,
 6214: 57,
 6233: 58,
 6300: 59,
 6488: 60,
 6641: 61,
 6933: 62,
 6975: 63,
 7015: 64,
 7089: 65,
 7099: 66,
 7407: 67,
 7645: 68,
 7884: 69,
 7899: 70,
 7919: 71,
 7971: 72,
 7975: 73,
 8011: 74,
 8111: 75,
 8194: 76,
 8213: 77,
 8371: 78,
 8567: 79,
 8709: 80,
 8747: 81,
 8911: 82,
 8942: 83,
 9308: 84,
 9426: 85,
 9482: 86,
 9508: 87,
 9610: 88,
 9618: 89,
 9734: 90,
 9908: 91,
 9959: 9

In [ ]:
np.diff(np.diff(list(item_original_ID_to_index_dict.values()))) is np.zeros(len(list(item_original_ID_to_index_dict.values())))# if are all 0 then it means that the IDs are ordered without any missin value => no need to translate

False

In [ ]:
#ICM_dataframe["UserID"] = [user_original_ID_to_index_dict[user_original] for user_original in
#                                      ICM_dataframe["UserID"].values]

ICM_dataframe["ItemID"] = [item_original_ID_to_index_dict[item_original] for item_original in 
                                      ICM_dataframe["ItemID"].values]

ICM_dataframe["FeatureID"] = [feature_original_ID_to_index_dict[feature_original] for feature_original in 
                                      ICM_dataframe["FeatureID"].values]

NameError: ignored

In [ ]:
n_users = len(user_original_ID_to_index_dict)
n_items = len(item_original_ID_to_index_dict)
#n_features = len(feature_original_ID_to_index_dict)

In [ ]:
URM_all = sps.csr_matrix((URM_all_dataframe["Interaction"].values, 
                          (URM_all_dataframe["UserID"].values, URM_all_dataframe["ItemID"].values)),
                        shape = (n_users, n_items))

URM_all

<13650x18059 sparse matrix of type '<class 'numpy.int64'>'
	with 5285664 stored elements in Compressed Sparse Row format>

In [ ]:
ICM_all = sps.csr_matrix((np.ones(len(ICM_dataframe["ItemID"].values)), 
                          (ICM_dataframe["ItemID"].values, ICM_dataframe["FeatureID"].values)),
                        shape = (n_items, n_features))

ICM_all.data = np.ones_like(ICM_all.data)

ICM_all

In [ ]:
ICM_all = sps.csr_matrix(ICM_all)
features_per_item = np.ediff1d(ICM_all.indptr)

ICM_all = sps.csc_matrix(ICM_all)
items_per_feature = np.ediff1d(ICM_all.indptr)

ICM_all = sps.csr_matrix(ICM_all)

In [ ]:
print(features_per_item.shape)
print(items_per_feature.shape)

NameError: ignored

In [ ]:
features_per_item = np.sort(features_per_item)
items_per_feature = np.sort(items_per_feature)

NameError: ignored

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

plt.rcParams["figure.figsize"]=(24, 5)

plt.plot(features_per_item, 'ro', markersize=2)
plt.ylabel('Num features ')
plt.xlabel('Sorted items')
plt.show()

In [ ]:
plt.plot(items_per_feature, 'ro', markersize=2)
plt.ylabel('Num items ')
plt.xlabel('Sorted features')
plt.show()

## Split data

In [ ]:
#!cat './Dataset/data_target_users_test.csv'

In [ ]:
test_UserID_path = os.path.join(data_file_path, "data_target_users_test.csv")

test_UserID_dataframe = pd.read_csv(filepath_or_buffer=test_UserID_path, 
                                    sep=",", 
                                    dtype={0:int},
                                    engine='python')

test_UserID_dataframe.columns = ["UserID"]

In [ ]:
len(test_UserID_dataframe) - n_users # see how many user should have the prediction

0

In [ ]:
test_UserID_number = test_UserID_dataframe.nunique()
test_UserID_number

UserID    13650
dtype: int64

In [ ]:
test_UserID_dataframe.head()

UserID
0       0
1       1
2       2
3       3
4       4

In [ ]:
test_UserID_array = test_UserID_dataframe.to_numpy().ravel().tolist()

## Fit

In [ ]:
def _get_instance(recommender_class, URM_train):

    recommender_object = recommender_class(URM_train)

    return recommender_object

In [ ]:
from Evaluation.Evaluator import EvaluatorHoldout
from Data_manager.split_functions.split_train_validation_random_holdout import split_train_in_two_percentage_global_sample

URM_train, URM_test = split_train_in_two_percentage_global_sample(URM_all, train_percentage = 0.80)
URM_train, URM_validation = split_train_in_two_percentage_global_sample(URM_train, train_percentage = 0.80)

evaluator_validation = EvaluatorHoldout(URM_validation, cutoff_list=[10])
evaluator_test = EvaluatorHoldout(URM_test, cutoff_list=[10], exclude_seen=True)

EvaluatorHoldout: Ignoring 13634 ( 0.1%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 13646 ( 0.0%) Users that have less than 1 test interactions


In [ ]:
print("Algorithm: {}".format(Random))

recommender_object = _get_instance(Random, URM_train)

recommender_object.fit()

results_run_1, results_run_string_1 = evaluator_test.evaluateRecommender(recommender_object)


items_scores = recommender_object._compute_item_score(user_id_array = test_UserID_array, items_to_compute = None)

Algorithm: <class 'Recommenders.NonPersonalizedRecommender.Random'>
EvaluatorHoldout: Processed 13646 (100.0%) in 14.84 sec. Users per second: 920


# Devi ordinare gli score per ottenere le recommendation, attento però alla memoria, cerca nei notebook del prof come ordinarli.

In [ ]:
items_scores

array([[4.30655531e-05, 8.68404650e-05, 1.01433923e-04, ...,
        9.99869520e-01, 9.99926349e-01, 9.99958857e-01],
       [1.23315220e-04, 2.01858501e-04, 3.22346531e-04, ...,
        9.99953146e-01, 9.99955793e-01, 9.99963264e-01],
       [5.89770449e-05, 1.11051952e-04, 1.29808849e-04, ...,
        9.99884202e-01, 9.99901284e-01, 9.99951169e-01],
       ...,
       [3.55929520e-06, 2.94112768e-05, 1.55191335e-04, ...,
        9.99936751e-01, 9.99943074e-01, 9.99958382e-01],
       [2.64780916e-05, 3.79840840e-05, 6.74902955e-05, ...,
        9.99735146e-01, 9.99748746e-01, 9.99820894e-01],
       [1.43667473e-04, 2.50606723e-04, 2.79995941e-04, ...,
        9.99969854e-01, 9.99982057e-01, 9.99989013e-01]])

In [ ]:
recommender_class_list = [
        Random,
        TopPop,
        GlobalEffects,
        #SLIMElasticNetRecommender,
        #UserKNNCFRecommender,
        #IALSRecommender,
        #MatrixFactorization_BPR_Cython,
        #MatrixFactorization_FunkSVD_Cython,
        #MatrixFactorization_AsySVD_Cython,
        #EASE_R_Recommender,
        #ItemKNNCFRecommender,
        #P3alphaRecommender,
        #SLIM_BPR_Cython,
        #RP3betaRecommender,
        #PureSVDRecommender,
        #NMFRecommender,
        #UserKNNCBFRecommender,
        #ItemKNNCBFRecommender,
        #UserKNN_CFCBF_Hybrid_Recommender,
        #ItemKNN_CFCBF_Hybrid_Recommender,
        #LightFMCFRecommender,
        #LightFMUserHybridRecommender,
        #LightFMItemHybridRecommender,
        ]



earlystopping_keywargs = {"validation_every_n": 5,
                          "stop_on_validation": True,
                          "evaluator_object": EvaluatorHoldout(URM_validation, [20], exclude_seen=True),
                          "lower_validations_allowed": 5,
                          "validation_metric": "MAP",
                         }

output_root_path = "./result_experiments/"

# If directory does not exist, create
if not os.path.exists(output_root_path):
  os.makedirs(output_root_path)


logFile = open(output_root_path + "result_all_algorithms.txt", "a")


for recommender_class in recommender_class_list:

        try:

            print("Algorithm: {}".format(recommender_class))

            recommender_object = _get_instance(recommender_class, URM_train)

            if isinstance(recommender_object, Incremental_Training_Early_Stopping):
                fit_params = {"epochs": 15, **earlystopping_keywargs}
            else:
                fit_params = {}

            recommender_object.fit(**fit_params)

            results_run_1, results_run_string_1 = evaluator_test.evaluateRecommender(recommender_object)

            recommender_object.save_model(output_root_path, file_name = "temp_model.zip")

            recommender_object = _get_instance(recommender_class, URM_train)
            recommender_object.load_model(output_root_path, file_name = "temp_model.zip")

            os.remove(output_root_path + "temp_model.zip")

            results_run_2, results_run_string_2 = evaluator_test.evaluateRecommender(recommender_object)

            if recommender_class not in [Random]:
                assert results_run_1.equals(results_run_2)

            print("Algorithm: {}, results: \n{}".format(recommender_class, results_run_string_1))
            logFile.write("Algorithm: {}, results: \n{}\n".format(recommender_class, results_run_string_1))
            logFile.flush()


        except Exception as e:
            traceback.print_exc()
            logFile.write("Algorithm: {} - Exception: {}\n".format(recommender_class, str(e)))
            logFile.flush()

EvaluatorHoldout: Ignoring 13644 ( 0.0%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 13645 ( 0.0%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 13645 ( 0.0%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 13644 ( 0.0%) Users that have less than 1 test interactions
Algorithm: <class 'Recommenders.NonPersonalizedRecommender.Random'>
RandomRecommender: URM Detected 1 ( 0.0%) items with no interactions.
EvaluatorHoldout: Processed 13645 (100.0%) in 12.51 sec. Users per second: 1090
RandomRecommender: Saving model in file './result_experiments/temp_model.zip'
RandomRecommender: Saving complete
RandomRecommender: URM Detected 1 ( 0.0%) items with no interactions.
RandomRecommender: Loading model from file './result_experiments/temp_model.zip'
RandomRecommender: Loading complete
EvaluatorHoldout: Processed 13645 (100.0%) in 13.14 sec. Users per second: 1039
Algorithm: <class 'Recommenders.NonPersonalizedRecomme

In [ ]:
from Recommenders.Similarity.Compute_Similarity_Python import Compute_Similarity_Python

similarity_object = Compute_Similarity_Python(ICM_all.T, 
                                              shrink=0.0,                ##################### hyper param
                                              topK=100,                  ##################### hyper param
                                              normalize=True, 
                                              similarity = "cosine")

W_sparse = similarity_object.compute_similarity()
W_sparse

# Write .csv for submission

In [ ]:
import csv

header = ['user_id','item_list']
csv_data = []

for user_id in test_user_ids:
    user_profile = URM_train[user_id]

    scores = user_profile.dot(W_sparse)
    scores = scores.toarray().ravel()
    
    ranking = scores.argsort()[::-1][0:10]
    csv_data.append([scores[ranking]])

In [ ]:
import csv

header = ['user_id','item_list']


data = [
    ['Albania', 28748, 'AL', 'ALB'],
    ['Algeria', 2381741, 'DZ', 'DZA'],
    ['American Samoa', 199, 'AS', 'ASM'],
    ['Andorra', 468, 'AD', 'AND'],
    ['Angola', 1246700, 'AO', 'AGO']
]

with open('countries.csv', 'w', encoding='UTF8', newline='') as f:
    writer = csv.writer(f)

    # write the header
    writer.writerow(header)

    # write multiple rows
    writer.writerows(data)

!cat countries.csv

In [ ]:
def prepare_submission(ratings: pd.DataFrame, users_to_recommend: np.array, urm_train: sp.csr_matrix, recommender: object):
    users_ids_and_mappings = ratings[ratings.user_id.isin(users_to_recommend)][["user_id", "mapped_user_id"]].drop_duplicates()
    items_ids_and_mappings = ratings[["item_id", "mapped_item_id"]].drop_duplicates()
    
    mapping_to_item_id = dict(zip(ratings.mapped_item_id, ratings.item_id))
    
    
    recommendation_length = 10
    submission = []
    for idx, row in users_ids_and_mappings.iterrows():
        user_id = row.user_id
        mapped_user_id = row.mapped_user_id
        
        recommendations = recommender.recommend(user_id=mapped_user_id,
                                                urm_train=urm_train,
                                                at=recommendation_length,
                                                remove_seen=True)
        
        submission.append((user_id, [mapping_to_item_id[item_id] for item_id in recommendations]))
        
    return submission

In [ ]:
def write_submission(submissions):
    with open("./submission.csv", "w") as f:
        for user_id, items in submissions:
            f.write(f"{user_id},{' '.join([str(item) for item in items])}\n")